In [12]:
import mlflow
# Step 2: Set up the MLflow tracking server
mlflow.set_tracking_uri("http://ec2-13-221-127-40.compute-1.amazonaws.com:5000/")

In [13]:
# Set or create an experiment
mlflow.set_experiment("Exp 6 - LightGBM HP Tuning")

<Experiment: artifact_location='s3://mlflow-bucket-youtube-sentiments-classifier/6', creation_time=1765528637240, experiment_id='6', last_update_time=1765528637240, lifecycle_stage='active', name='Exp 6 - LightGBM HP Tuning', tags={}>

In [14]:
import mlflow
import mlflow.sklearn
import optuna
import pandas as pd
import matplotlib.pyplot as plt

from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score, classification_report
from imblearn.over_sampling import SMOTE
from lightgbm import LGBMClassifier

In [15]:
import pandas as pd

df = pd.read_csv('reddit_preprocessing.csv').dropna()
df.shape

(36662, 2)

In [16]:
# Step 1: Remap the class labels from [-1, 0, 1] to [2, 0, 1]
df['category'] = df['category'].map({-1: 2, 0: 0, 1: 1})

# Step 2: Remove rows where the target labels (category) are NaN
df = df.dropna(subset=['category'])

In [17]:
# Step 3: TF-IDF vectorizer setup
ngram_range = (1, 3)  # Trigram
max_features = 1000  # Set max_features to 1000
vectorizer = TfidfVectorizer(ngram_range=ngram_range, max_features=max_features)
X = vectorizer.fit_transform(df['clean_comment'])
y = df['category']

# Step 4: Apply SMOTE to handle class imbalance
smote = SMOTE(random_state=42)
X_resampled, y_resampled = smote.fit_resample(X, y)

In [18]:
# Step 5: Train-test split
X_train, X_test, y_train, y_test = train_test_split(X_resampled, y_resampled, test_size=0.2, random_state=42, stratify=y_resampled)

In [19]:
# Function to log results in MLflow
def log_mlflow(model_name, model, X_train, X_test, y_train, y_test, params, trial_number):
    with mlflow.start_run(run_name=f"Trial_{trial_number}_{model_name}_SMOTE_TFIDF_Trigrams"):
        mlflow.set_tag("experiment_type", "algorithm_comparison")
        mlflow.log_param("algo_name", model_name)

        # Log hyperparameters
        for key, value in params.items():
            mlflow.log_param(key, value)

        # Train model
        model.fit(X_train, y_train)
        y_pred = model.predict(X_test)

        # Log accuracy
        accuracy = accuracy_score(y_test, y_pred)
        mlflow.log_metric("accuracy", accuracy)

        # Log classification report
        classification_rep = classification_report(y_test, y_pred, output_dict=True)
        for label, metrics in classification_rep.items():
            if isinstance(metrics, dict):
                for metric, value in metrics.items():
                    mlflow.log_metric(f"{label}_{metric}", value)

        # Log the model
        mlflow.sklearn.log_model(model, f"{model_name}_model")

        return accuracy


In [20]:
# Optuna objective function
def objective_lightgbm(trial):
    params = {
        'n_estimators': trial.suggest_int('n_estimators', 100, 1000),
        'learning_rate': trial.suggest_float('learning_rate', 1e-4, 1e-1, log=True),
        'max_depth': trial.suggest_int('max_depth', 3, 15),
        'num_leaves': trial.suggest_int('num_leaves', 20, 150),
        'min_child_samples': trial.suggest_int('min_child_samples', 10, 100),
        'colsample_bytree': trial.suggest_float('colsample_bytree', 0.5, 1.0),
        'subsample': trial.suggest_float('subsample', 0.5, 1.0),
        'reg_alpha': trial.suggest_float('reg_alpha', 1e-4, 10.0, log=True),
        'reg_lambda': trial.suggest_float('reg_lambda', 1e-4, 10.0, log=True),
    }

    model = LGBMClassifier(**params, random_state=42)
    accuracy = log_mlflow("LightGBM", model, X_train, X_test, y_train, y_test, params, trial.number)
    return accuracy

In [21]:
# Run Optuna experiment
def run_optuna_experiment():
    study = optuna.create_study(direction="maximize")
    study.optimize(objective_lightgbm, n_trials=100)

    best_params = study.best_params
    best_model = LGBMClassifier(**best_params, random_state=42)

    log_mlflow("LightGBM", best_model, X_train, X_test, y_train, y_test, best_params, "Best")

    # Visualization (works in Jupyter; for scripts, save instead)
    optuna.visualization.plot_param_importances(study).show()
    optuna.visualization.plot_optimization_history(study).show()

In [22]:
# Run the experiment for LightGBM
run_optuna_experiment()

[I 2025-12-12 14:23:01,225] A new study created in memory with name: no-name-af130b56-f462-47ca-af23-31c4e5176741
D:\Youtube-Sentiments-Classifier-End-to-End\.venv\Lib\site-packages\sklearn\utils\deprecation.py:132: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(


[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.078872 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 98828
[LightGBM] [Info] Number of data points in the train set: 37848, number of used features: 958
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further s

D:\Youtube-Sentiments-Classifier-End-to-End\.venv\Lib\site-packages\sklearn\utils\deprecation.py:132: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
2025/12/12 14:24:03 WARNING mlflow.models.model: Model logged without a signature and input example. Please set `input_example` parameter when logging the model to auto infer the model signature.
2025/12/12 14:25:16 INFO mlflow.tracking._tracking_service.client: 🏃 View run Trial_0_LightGBM_SMOTE_TFIDF_Trigrams at: http://ec2-13-221-127-40.compute-1.amazonaws.com:5000/#/experiments/6/runs/1aab2f663c194d0cb2f9b73f6e8436a1.
2025/12/12 14:25:16 INFO mlflow.tracking._tracking_service.client: 🧪 View experiment at: http://ec2-13-221-127-40.compute-1.amazonaws.com:5000/#/experiments/6.
[I 2025-12-12 14:25:16,656] Trial 0 finished with value: 0.7595645740858169 and parameters: {'n_estimators': 867, 'learning_rate': 0.005604083951813162, 'max_depth': 9, 'num_leaves': 114, 'min

[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.077890 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 99009
[LightGBM] [Info] Number of data points in the train set: 37848, number of used features: 969
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further s

D:\Youtube-Sentiments-Classifier-End-to-End\.venv\Lib\site-packages\sklearn\utils\deprecation.py:132: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
2025/12/12 14:26:27 WARNING mlflow.models.model: Model logged without a signature and input example. Please set `input_example` parameter when logging the model to auto infer the model signature.
2025/12/12 14:27:09 INFO mlflow.tracking._tracking_service.client: 🏃 View run Trial_1_LightGBM_SMOTE_TFIDF_Trigrams at: http://ec2-13-221-127-40.compute-1.amazonaws.com:5000/#/experiments/6/runs/208c3e60e1a64665a1e368cebe5f4d8d.
2025/12/12 14:27:09 INFO mlflow.tracking._tracking_service.client: 🧪 View experiment at: http://ec2-13-221-127-40.compute-1.amazonaws.com:5000/#/experiments/6.
[I 2025-12-12 14:27:09,716] Trial 1 finished with value: 0.6613823715916297 and parameters: {'n_estimators': 760, 'learning_rate': 0.00018256210916826632, 'max_depth': 12, 'num_leaves': 92, 'm

...

[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.077311 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 98991
[LightGBM] [Info] Number of data points in the train set: 37848, number of used features: 967
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further s

D:\Youtube-Sentiments-Classifier-End-to-End\.venv\Lib\site-packages\sklearn\utils\deprecation.py:132: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
2025/12/12 15:42:39 WARNING mlflow.models.model: Model logged without a signature and input example. Please set `input_example` parameter when logging the model to auto infer the model signature.
2025/12/12 15:43:16 INFO mlflow.tracking._tracking_service.client: 🏃 View run Trial_32_LightGBM_SMOTE_TFIDF_Trigrams at: http://ec2-13-221-127-40.compute-1.amazonaws.com:5000/#/experiments/6/runs/b41615bd1556421496d2006a44ed1e73.
2025/12/12 15:43:16 INFO mlflow.tracking._tracking_service.client: 🧪 View experiment at: http://ec2-13-221-127-40.compute-1.amazonaws.com:5000/#/experiments/6.
[I 2025-12-12 15:43:17,142] Trial 32 finished with value: 0.8171633904037201 and parameters: {'n_estimators': 937, 'learning_rate': 0.05299813087635911, 'max_depth': 15, 'num_leaves': 54, 'mi

[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.077364 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 99001
[LightGBM] [Info] Number of data points in the train set: 37848, number of used features: 968
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further s

D:\Youtube-Sentiments-Classifier-End-to-End\.venv\Lib\site-packages\sklearn\utils\deprecation.py:132: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
2025/12/12 15:44:11 WARNING mlflow.models.model: Model logged without a signature and input example. Please set `input_example` parameter when logging the model to auto infer the model signature.
[W 2025-12-12 15:50:06,011] Trial 33 failed with parameters: {'n_estimators': 715, 'learning_rate': 0.026285737556424087, 'max_depth': 11, 'num_leaves': 53, 'min_child_samples': 24, 'colsample_bytree': 0.5036987345283499, 'subsample': 0.5552418213692347, 'reg_alpha': 0.0006460359843929025, 'reg_lambda': 0.0037761843581023305} because of the following error: MlflowException('API request to http://ec2-13-221-127-40.compute-1.amazonaws.com:5000/api/2.0/mlflow/runs/get failed with exception HTTPConnectionPool(host=\'ec2-13-221-127-40.compute-1.amazonaws.com\', port=5000): Max re

MlflowException: API request to http://ec2-13-221-127-40.compute-1.amazonaws.com:5000/api/2.0/mlflow/runs/get failed with exception HTTPConnectionPool(host='ec2-13-221-127-40.compute-1.amazonaws.com', port=5000): Max retries exceeded with url: /api/2.0/mlflow/runs/get?run_uuid=90f91c29cdd643f7af7225735de62bee&run_id=90f91c29cdd643f7af7225735de62bee (Caused by NewConnectionError("HTTPConnection(host='ec2-13-221-127-40.compute-1.amazonaws.com', port=5000): Failed to establish a new connection: [WinError 10061] No connection could be made because the target machine actively refused it"))